# Sample Code for Training Multiclass Classroom Management Classification Measures

This notebook provides sample code for training multiclass classification measures using the classroom management datasets included in the collection. It is intended as a minimal example for researchers.

## Notes
This code uses the SimpleTransformers library, and the base model is RoBERTa. You can change the base model or experiment with hyperparameters here, though our paper [1] uses the defaults.


## How to Run
Download the "talkmoves.csv" file in the collection and process it so that you select the "text" and "vs_submove" columns. Rename the "vs_submoves" column "labels". You should have two columns, "text" and "labels". All other files and columns should be used with the binary classification notebook.

## Author
Mei Tan, EduNLP Lab @ Stanford University Graduate School of Education, 2024

[1] Tan, Mei, and Dorottya Demszky. (2025). Do As I Say: What Teachers’ Language Reveals About Classroom
Management Practices. (EdWorkingPaper: 23-844). Retrieved from Annenberg Institute at Brown University:
https://doi.org/10.26300/9yj6-jn52

In [ ]:
import pandas as pd
train_data = pd.read_csv("<YOUR DATA PATH HERE>")

In [ ]:
!pip install --upgrade transformers
!pip install --upgrade simpletransformers
from simpletransformers.classification import ClassificationModel, ClassificationArgs
from sklearn.metrics import precision_score, recall_score, f1_score
from sklearn.model_selection import KFold, train_test_split
from scipy.stats import pearsonr, spearmanr
import warnings
import numpy as np
import pandas as pd
from sys import exit
import logging
import torch
import wandb
warnings.filterwarnings("ignore")
transformers_logger = logging.getLogger("transformers")
transformers_logger.setLevel(logging.WARNING)

wandbproject = "<ANY STRING TO NAME W AND B RUN HERE>"
output_dir = "<NAME YOUR OUTPUT FOLDER HERE>"

In [ ]:
def precision_multiclass(preds, labels):
    per_class_precision = precision_score(y_true=labels, y_pred=preds, average=None)
    macro_precision = np.mean(per_class_precision)
    for i, p in enumerate(per_class_precision):
        wandb.log({f"Precision_Class_{i}": p})
        print(p)

    return macro_precision

def recall_multiclass(preds, labels):
    per_class_recall = recall_score(y_true=labels, y_pred=preds, average=None)
    macro_recall = np.mean(per_class_recall)
    for i, r in enumerate(per_class_recall):
        wandb.log({f"Recall_Class_{i}": r})
        print(r)

    return macro_recall

def f1_multiclass(preds, labels):
    per_class_f1 = f1_score(y_true=labels, y_pred=preds, average=None)
    macro_f1 = np.mean(per_class_f1)
    for i, f in enumerate(per_class_f1):
        wandb.log({f"F1_Class_{i}": f})
        print(f)

    return macro_f1

In [ ]:
def train_multiclass(label_name, label_col, text_col, train_df, eval_df, output_dir,
          model="roberta",
          num_labels=4,
          num_train_epochs=5,
          train_batch_size=8,
          gradient_accumulation_steps=2,
          max_seq_length=512,
          cross_validate=False,
          balance_labels_oversample=False,
          balance_labels_weights=False,
          weights = None):

    if balance_labels_oversample:
        most_common = train_df[label_col].value_counts().idxmax()
        most_common_df = train_df[train_df[label_col]==most_common]
        concat_list = [most_common_df]
        for label, group in train_df[train_df[label_col]!=most_common].groupby(label_col):
            concat_list.append(group.sample(replace=True, n=len(most_common_df)))
        train_df = pd.concat(concat_list)

    train_df = train_df.sample(frac=1)
    save_dir = output_dir + "/" + label_name + "_train_size=" + str(len(train_df))

    model_args = ClassificationArgs()
    model_args.reprocess_input_data = True
    model_args.overwrite_output_dir = True
    model_args.evaluate_during_training = True
    model_args.max_seq_length = int(max_seq_length / len(text_col))
    model_args.num_train_epochs = num_train_epochs
    model_args.evaluate_during_training_steps = int(len(train_df) / train_batch_size) # after each epoch
    model_args.save_eval_checkpoints = False
    model_args.save_model_every_epoch = False
    model_args.wandb_project = label_name
    model_args.train_batch_size = train_batch_size
    model_args.output_dir = save_dir
    model_args.best_model_dir = save_dir +"/best_model"
    model_args.cache_dir = save_dir + "/cache"
    model_args.tensorboard_dir = save_dir + "/tensorboard"
    model_args.regression = num_labels == 1
    model_args.gradient_accumulation_steps = gradient_accumulation_steps
    model_args.wandb_kwargs = {"reinit": True}
    model_args.fp16 = False
    model_args.fp16_opt_level = "O0"
    model_args.no_cache = False
    model_args.no_save = cross_validate
    model_args.save_optimizer_and_scheduler = True

    if balance_labels_weights:
      model = ClassificationModel(model.split("-")[0], model,
                                use_cuda=torch.cuda.is_available(),
                                num_labels=num_labels,
                                args=model_args, weight=weights)
    else:
      model = ClassificationModel(model.split("-")[0], model,
                                use_cuda=torch.cuda.is_available(),
                                num_labels=num_labels,
                                args=model_args)

    train_args = {"use_multiprocessing": False,
                            "process_count": 1,
                            "use_multiprocessing_for_evaluation": False}
    if wandb.run is not None:
      wandb.finish()
    model.train_model(train_df,
                      eval_df=eval_df,
                      precision=precision_multiclass,
                      recall=recall_multiclass,
                      f1=f1_multiclass,
                      args=train_args)
    return model

In [ ]:
def predict(fname, model_path, model=None,
            model_type="roberta-base", predict_list=None,
          index_list=None, index_colname="index"):

    preds, outputs = model.predict(predict_list)
    with open(model_path + '/' + fname + '_preds.txt', 'w') as f:
        f.write(f"{index_colname}\tpred\outputs\n")
        for index, pred, output in zip(index_list, preds, outputs):
            f.write(f"{index}\t{pred}\t{output}\n")

    return preds

In [ ]:
# Sample Train
model = train_multiclass(wandbproject, "labels", "text", train_data, train_data,  output_dir=output_dir,
                model="roberta-base", num_labels=4, balance_labels_oversample=True, cross_validate=False)

In [ ]:
# Sample Predict
predict_data = pd.read_csv("<YOUR DATA PATH HERE>")
predict_list = predict_data['text'].tolist()
index_list = predict_data['index'].tolist()
predict(wandbproject, "predictions", model, model_type="roberta-base", predict_list=predict_list,
        index_list=index_list, index_colname="index")